# Data

I used `bedtools` to intersect constrained coding regions (CCRs), defined by exonic regions lying between consecutive non-synonymous [gnomAD](http://gnomad.broadinstitute.org/) variants, with somatic mutations observed in cancer genomes ([COSMIC](https://cancer.sanger.ac.uk/cosmic/download)). The result of this analysis is a `pickle` file containing the total multi-exonic length,  number of somatic mutations, and other "features" (e.g. CpG density and synonymous variant density) for each CCR:

In [1]:
import pandas as pd
data_df = pd.read_pickle('ccrs.v2.20180420.lengths_numberMutations.pkl')
data_df.head()

unique_key  total_number_of_mutations  total_length  chrom     ccr_pct  \
0           1                         33           338      4  100.000000   
1           2                         21           319      2   99.997902   
2           3                         79           295      1   99.997028   
3           4                         58           290      4   99.995827   
4           5                         32           295      2   99.994760   

     gene                                             ranges  \
0   DHX15  24541797-24541922,24542462-24542571,24543495-2...   
1   SF3B1            198257731-198257912,198260779-198260917   
2    PBX1  164769048-164769126,164776778-164776914,164781...   
3  UBE2D3  103720577-103720657,103722610-103722716,103723...   
4   SF3B1  198267496-198267550,198267672-198267759,198268...   

                               varflag  syn_density   cpg  cov_score   resid  \
0           VARFALSE,VARFALSE,VARFALSE        0.068  0.02     335.59  46.489   
1                    VARFALSE,VARFALSE        0.088  0.03     318.98  44.129   
2           VARFALSE,VARFALSE,VARFALSE        0.088  0.09     295.00  40.662   
3  VARFALSE,VARFALSE,VARFALSE,VARFALSE        0.066  0.02     286.98  39.622   
4           VARFALSE,VARFALSE,VARFALSE        0.037  0.04     280.62  38.697   

   resid_pctile  
0    100.000000  
1     95.141301  
2     88.002426  
3     85.860636  
4     83.956102

# Modeling 

Before describing how the data is modeled, let's make the modules containing the modeling code visible to the Notebook:


In [2]:
import sys
sys.path.append('/Users/petermchale/Work/germline_vs_somatic_constraint/model')
print 'Python searches these paths when asked to import a module:'
for path in sys.path: 
    print(path)

Python searches these paths when asked to import a module:

/anaconda2/envs/tensorflow/lib/python27.zip
/anaconda2/envs/tensorflow/lib/python2.7
/anaconda2/envs/tensorflow/lib/python2.7/plat-darwin
/anaconda2/envs/tensorflow/lib/python2.7/plat-mac
/anaconda2/envs/tensorflow/lib/python2.7/plat-mac/lib-scriptpackages
/anaconda2/envs/tensorflow/lib/python2.7/lib-tk
/anaconda2/envs/tensorflow/lib/python2.7/lib-old
/anaconda2/envs/tensorflow/lib/python2.7/lib-dynload
/anaconda2/envs/tensorflow/lib/python2.7/site-packages
/anaconda2/envs/tensorflow/lib/python2.7/site-packages/IPython/extensions
/Users/petermchale/.ipython
/Users/petermchale/Work/germline_vs_somatic_constraint/model


I assume the mutations are Poisson distributed with an average mutation count equal to $lh(x)$ where $l$ is interval length, $x$ is some feature, and a $h$ is a neural network $h(x)$ modeling the unknown mutation rate: 

In [3]:
# train the model using tensorflow
from neural_network import train
data_df_headings = {'l_heading_list': ['total_length'],
                    'X_heading_list': ['syn_density'],
                    'y_heading_list': ['total_number_of_mutations']}
log_df = train(data_df, **data_df_headings)
log_df

Instructions for updating:
Use the retry module or similar alternatives.


epoch      cost  likelihood      bias    weight
0     0.0  5.119138         0.0 -0.100000 -1.154452
1    10.0  1.955872         0.0 -1.021427 -2.051607
2    20.0  1.335888         0.0 -1.663376 -2.580997
3    30.0  1.273747         0.0 -2.006990 -2.725168
4    40.0  1.281000         0.0 -2.140706 -2.604419
5    50.0  1.272261         0.0 -2.156888 -2.335146
6    60.0  1.261261         0.0 -2.123763 -1.999845
7    70.0  1.248822         0.0 -2.084825 -1.651711
8    80.0  1.238944         0.0 -2.062488 -1.321271
9    90.0  1.234305         0.0 -2.062222 -1.020805
10  100.0  1.228636         0.0 -2.078614 -0.749729
11  110.0  1.228968         0.0 -2.102587 -0.501917
12  120.0  1.223022         0.0 -2.126895 -0.272086
13  130.0  1.218581         0.0 -2.148124 -0.058706
14  140.0  1.217235         0.0 -2.165920  0.136578
15  150.0  1.216091         0.0 -2.181245  0.311081
16  160.0  1.216228         0.0 -2.194996  0.462976
17  170.0  1.216145         0.0 -2.207490  0.592099
18  180.0  1.213698         0.0 -2.218607  0.699744
19  190.0  1.213025         0.0 -2.228124  0.788009
20  200.0  1.213741         0.0 -2.235962  0.859228
21  210.0  1.214539         0.0 -2.242223  0.915693
22  220.0  1.214457         0.0 -2.247124  0.959605
23  230.0  1.214167         0.0 -2.250899  0.993072
24  240.0  1.214052         0.0 -2.253756  1.018075
25  250.0  1.213646         0.0 -2.255875  1.036402
26  260.0  1.213838         0.0 -2.257405  1.049587
27  270.0  1.213927         0.0 -2.258484  1.058892
28  280.0  1.213905         0.0 -2.259237  1.065325
29  290.0  1.213896         0.0 -2.259748  1.069684

# Analysis of learned model 

In [4]:
data_df_sampled = data_df.sample(frac=0.01, random_state=0)

%matplotlib inline 

from plot import plot_counts
plot_counts(data_df_sampled, **data_df_headings)

# Modeling the mutation rate 

We assume that the above mutation-count data were generated by a Poisson process with a count function $H_\theta(l, x) = lh_\theta(x)$, where 
$l$ is the length of a CCR, $x$ is a feature (e.g. CpG density), and
$\theta$ is a  parameter vector that dictates the form of the function. 



Features such as CpG density are assumed to be non-noisy. Yet a computation of CpG density from a very small CCR is subject to sampling noise, e.g. the CpG density of a CCR of length 2 can only be 0 or 1. In an effort to average out this noise, I restricted the analysis to CCRs of length larger than a threshold value:

In [5]:
# df = df[df.total_length>20]
sample_size = len(df)

NameError: name 'df' is not defined

I will represent $h_\theta(x)$, the estimated mutation rate, by a neural network, since neural networks have the capacity to represent any function. In the spirit of choosing the simplest model possible, I will consider the special case of [Poisson Regression](https://en.wikipedia.org/wiki/Poisson_regression), which can be viewed as a neural network that has no hidden layers and an activation function (called an inverse link function in the generalized-linear-model literature) equal to: 

\begin{equation}
h_\theta(x) =  e^{b + Wx} ,
\end{equation}

where $\theta = (b, W)$. The exponential guarantees that the rate is non-negative, as it must be. 



In [ ]:
import tensorflow as tf
import os 

# turn off tensorflow warning messages 
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '2'

number_exposure_input_nodes = 1 # the "l"s are called "exposures" in the Poisson regression literature
number_feature_input_nodes = 1 # can be increased as more features are added
number_hidden_nodes = 1 # can be increased to go beyond Poisson regression
number_output_nodes = 1

tf.set_random_seed(1)

# use "variable scopes" to help tensorflow produce readable diagrams of the computational graph in tensorboard: 

# exposure input
with tf.variable_scope('exposure_input_layer'): 
    l = tf.placeholder(tf.float32, shape=(sample_size, number_exposure_input_nodes)) 

# feature inputs 
with tf.variable_scope('feature_input_layer'): 
    X = tf.placeholder(tf.float32, shape=(sample_size, number_feature_input_nodes)) 
    
# hidden layer (placeholder for later development beyond Poisson regression)
with tf.variable_scope('hidden_layer'): 
    hidden_layer_output = X 
    
# output layer
with tf.variable_scope('output_layer'): 
    weights = tf.get_variable(name="output_weights", 
                              shape=(number_hidden_nodes, number_output_nodes),
                              initializer=tf.contrib.layers.xavier_initializer()) 
    biases = tf.get_variable(name="output_biases", 
                             shape=number_output_nodes,
                             initializer=tf.zeros_initializer())    
    h = tf.exp(tf.matmul(hidden_layer_output, weights) + biases)
    prediction = l*h

# Cost function

We attempt to reconstruct the true mutation rate by the principle of maximum likelihood. The corresponding objective function to minimize is: 

\begin{equation}
{\cal L}(\theta \, | \, x_1, \ldots, x_m; l_1, \ldots, l_m; n_1, \ldots, n_m) = \frac{1}{m} \sum_{i=1}^m \left[ \, 
H_i(\theta) - n_i \log H_i(\theta) + \log \left( n_i! \right)
\, \right] ,
\end{equation}

where $H_i(\theta) = l_i h_\theta(x_i)$ is the "predicted" count for CCR $i$ and $n_i$ is the "actual"  count. 




In [ ]:
with tf.variable_scope('cost'):
    y = tf.placeholder(tf.float32, shape=(sample_size, 1))
    cost = tf.reduce_mean(prediction - y*tf.log(prediction+1e-10) + tf.lgamma(y+1.0))

# Training the model

In [ ]:
import numpy as np

feed_dict = {l:df[['total_length']].values, 
             X:df[['cpg']].values, 
             y:df[['total_number_of_mutations']].values}

with tf.variable_scope('train'): 
    training_step = tf.train.AdamOptimizer(learning_rate=0.1).minimize(cost)
    
log_df = pd.DataFrame(columns=['epoch', 'cost', 'likelihood', 'bias', 'weight'])
i = 0

with tf.Session() as session: 
    session.run(tf.global_variables_initializer())     
    for epoch in range(300): 
        _, cost_eval, prediction_eval, h_eval = session.run([training_step, cost, prediction, h], feed_dict=feed_dict)
        if epoch % 10 == 0: 
            bias_eval = float(biases.eval())
            weight_eval = float(weights.eval())
            log_df.loc[i] = [epoch, 
                             cost_eval, 
                             np.exp(-sample_size*cost_eval), 
                             bias_eval, 
                             weight_eval]
            i += 1

The cost decreases as the network is trained on the data: 

In [ ]:
log_df

# Detecting outliers

This compares the observed mutation count $n_i$ for CCR $i$ with its expected count $H_i(\theta)$:


In [ ]:
%matplotlib inline
df.hist(column='syn_density')

In [ ]:
df.head()

In [ ]:
import plotly
plotly.offline.init_notebook_mode(connected=True)

df['expected_mutation_count'] = prediction_eval
df['expected_mutation_rate'] = h_eval
df_sampled = df.sample(frac=0.01, random_state=0)

def scatter_plot(): 
    trace1 = plotly.graph_objs.Scattergl(
        x=df_sampled.total_number_of_mutations, 
        y=df_sampled.expected_mutation_count,
        mode='markers', 
        marker=dict(
            size=10,
            line=dict(width=1.5)),
        text=['gene: {}<br>length: {}<br>cpg: {:.3}<br>syn_density: {:.2}<br>cov_score: {}<br>resid_pctile: {}'.format(
            g, int(l), x, s, c, p) for g, l, x, s, c, p in zip(df_sampled.gene, 
                                                              df_sampled.total_length, 
                                                              df.cpg, 
                                                              df.syn_density,
                                                              df.cov_score,
                                                              df.resid_pctile)],
        hoverinfo='text') # WebGL can render a large number of data points

    a = np.arange(df_sampled.total_number_of_mutations.max())
    trace2 = plotly.graph_objs.Scattergl(x=a, y=a)
    
    data = [trace1, trace2]

    layout = dict(title='somatic mutation counts',
                  font=dict(size=20),
                  hovermode='closest',
                  xaxis=dict(title='observed', type='log'),
                  yaxis=dict(title='expected', type='log'),
                  showlegend=False)

    fig = dict(data=data, layout=layout)
    plotly.offline.iplot(fig)
    
scatter_plot()

# TO DO

* HARD: plot expected versus observed **order statistics** of counts (QQ plot; see 4.ipynb)
* do above with 0, 1, and 2 features (reproduce QQ plot in 4.ipynb)

